In [1]:
from sqlalchemy import create_engine, String, ForeignKey
from sqlalchemy.orm import (
    DeclarativeBase,
    MappedAsDataclass,
    Mapped,
    mapped_column,
    relationship,
)


class Base(MappedAsDataclass, DeclarativeBase):
    pass


class ComponentCategory(Base):
    __tablename__ = "component_category"

    id: Mapped[int] = mapped_column(primary_key=True, init=False)
    name: Mapped[str] = mapped_column(String(20))

    variants: Mapped[list["ComponentCategoryVariant"]] = relationship(
        back_populates="category", default_factory=list
    )
    components: Mapped[list["Component"]] = relationship(
        back_populates="category", default_factory=list
    )


class ComponentCategoryVariant(Base):
    __tablename__ = "component_category_variant"

    id: Mapped[int] = mapped_column(primary_key=True, init=False)
    category_id: Mapped[int] = mapped_column(
        ForeignKey("component_category.id"), init=False
    )
    content: Mapped[bytes]

    category: Mapped["ComponentCategory"] = relationship(
        back_populates="variants", default=None
    )


class Component(Base):
    __tablename__ = "component"

    id: Mapped[int] = mapped_column(primary_key=True, init=False)
    page_id: Mapped[int] = mapped_column(ForeignKey("page.id"), init=False)
    category_id: Mapped[int] = mapped_column(
        ForeignKey("component_category.id"), init=False
    )
    content: Mapped[bytes]
    x: Mapped[int]
    y: Mapped[int]
    w: Mapped[int]
    h: Mapped[int]

    category: Mapped["ComponentCategory"] = relationship(
        back_populates="components", default=None
    )
    page: Mapped["Page"] = relationship(back_populates="components", default=None)


class Page(Base):
    __tablename__ = "page"

    id: Mapped[int] = mapped_column(primary_key=True, init=False)
    content: Mapped[bytes]

    components: Mapped[list["Component"]] = relationship(
        back_populates="page", default_factory=list
    )


engine = create_engine("sqlite:///nmn.db", echo=True)
Base.metadata.create_all(engine)

2023-12-29 21:47:11,741 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2023-12-29 21:47:11,742 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("component_category")
2023-12-29 21:47:11,743 INFO sqlalchemy.engine.Engine [raw sql] ()
2023-12-29 21:47:11,744 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("component_category")
2023-12-29 21:47:11,745 INFO sqlalchemy.engine.Engine [raw sql] ()
2023-12-29 21:47:11,746 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("component_category_variant")
2023-12-29 21:47:11,747 INFO sqlalchemy.engine.Engine [raw sql] ()
2023-12-29 21:47:11,747 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("component_category_variant")
2023-12-29 21:47:11,748 INFO sqlalchemy.engine.Engine [raw sql] ()
2023-12-29 21:47:11,749 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("component")
2023-12-29 21:47:11,749 INFO sqlalchemy.engine.Engine [raw sql] ()
2023-12-29 21:47:11,750 INFO sqlalchemy.engine.Engine PRAGMA temp.table_info("component")
20

In [2]:
import sys

sys.path.insert(0, "../lib")

from component_classification import (
    generate_categories,
    generate_components,
    classify_components,
)

paths, contents = generate_categories()
# components = generate_components()
# results = classify_components(components, categories)

In [3]:
# numpy array to bytes and back

import numpy as np
from io import BytesIO


def numpy_to_bytes(arr: np.ndarray) -> bytes:
    with BytesIO() as f:
        np.save(f, arr)
        return f.getvalue()


def bytes_to_numpy(b: bytes) -> np.ndarray:
    with BytesIO(b) as f:
        return np.load(f)

In [4]:
# insert categories and its variants

from sqlalchemy.orm import sessionmaker

Session = sessionmaker(bind=engine)

segments = [path.stem.split(".") for path in paths]
category_names = {s[0] for s in segments}
categories = {name: ComponentCategory(name) for name in category_names}
variants = []

for s, c in zip(segments, contents):
    variant = ComponentCategoryVariant(content=numpy_to_bytes(c))
    categories[s[0]].variants.append(variant)
    variants.append(variant)

In [5]:
with Session() as session:
    session.expire_on_commit = False
    session.add_all(categories.values())
    session.commit()

2023-12-29 21:47:12,288 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2023-12-29 21:47:12,293 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,293 INFO sqlalchemy.engine.Engine [generated in 0.00061s] ('5',)
2023-12-29 21:47:12,295 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,295 INFO sqlalchemy.engine.Engine [cached since 0.002693s ago] ('1',)
2023-12-29 21:47:12,296 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,298 INFO sqlalchemy.engine.Engine [cached since 0.005135s ago] ('lparen',)
2023-12-29 21:47:12,299 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,300 INFO sqlalchemy.engine.Engine [cached since 0.007422s ago] ('P',)
2023-12-29 21:47:12,301 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,302 INFO sqlalchemy.engine.Engine 

2023-12-29 21:47:12,354 INFO sqlalchemy.engine.Engine [cached since 0.06155s ago] ('s',)
2023-12-29 21:47:12,360 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,361 INFO sqlalchemy.engine.Engine [cached since 0.06854s ago] ('9',)
2023-12-29 21:47:12,362 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,363 INFO sqlalchemy.engine.Engine [cached since 0.07025s ago] ('hbar_l',)
2023-12-29 21:47:12,364 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,365 INFO sqlalchemy.engine.Engine [cached since 0.07204s ago] ('J',)
2023-12-29 21:47:12,365 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,366 INFO sqlalchemy.engine.Engine [cached since 0.07321s ago] ('E',)
2023-12-29 21:47:12,367 INFO sqlalchemy.engine.Engine INSERT INTO component_category (name) VALUES (?)
2023-12-29 21:47:12,367 INFO sqlalc

In [6]:
from component_classification import get_components, classify_components

from pathlib import Path

import cv2 as cv
from sqlalchemy import select

pages = []
targets = [bytes_to_numpy(v.content) for v in variants]

for path in Path("scores/").iterdir():
    print(path)
    img = cv.imread(str(path))
    coords, components = get_components(img)

    results = classify_components(components, targets)

    with Session(expire_on_commit=False) as session:
        page = Page(content=numpy_to_bytes(img))
        for (i, row), content in zip(coords.iterrows(), components):
            component = Component(numpy_to_bytes(content), row.x, row.y, row.w, row.h)
            component.category = categories[variants[results[i]].category.name]
            component.page = page
            session.add(component)

        session.add(page)
        session.commit()

scores/qiqin_l1.png


2023-12-29 21:47:23,007 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2023-12-29 21:47:23,009 INFO sqlalchemy.engine.Engine INSERT INTO page (content) VALUES (?)
2023-12-29 21:47:23,010 INFO sqlalchemy.engine.Engine [generated in 0.00059s] (<memory at 0x7fc6bc2afc40>,)
2023-12-29 21:47:23,100 INFO sqlalchemy.engine.Engine INSERT INTO component (page_id, category_id, content, x, y, w, h) VALUES (?, ?, ?, ?, ?, ?, ?)
2023-12-29 21:47:23,101 INFO sqlalchemy.engine.Engine [generated in 0.00086s] (1, 38, <memory at 0x7fc6bc2afc40>, 0, 0, 1680, 2547)
2023-12-29 21:47:23,119 INFO sqlalchemy.engine.Engine INSERT INTO component (page_id, category_id, content, x, y, w, h) VALUES (?, ?, ?, ?, ?, ?, ?)
2023-12-29 21:47:23,120 INFO sqlalchemy.engine.Engine [cached since 0.01949s ago] (1, 31, <memory at 0x7fc6bc2afdc0>, 620, 107, 57, 98)
2023-12-29 21:47:23,121 INFO sqlalchemy.engine.Engine INSERT INTO component (page_id, category_id, content, x, y, w, h) VALUES (?, ?, ?, ?, ?, ?, ?)
2023-12-29 21: